In [1]:
from theano.sandbox import cuda
cuda.use('gpu2')

WARNING (theano.sandbox.cuda): The cuda backend is deprecated and will be removed in the next release (v0.10).  Please switch to the gpuarray backend. You can get more information about how to switch at this URL:
 https://github.com/Theano/Theano/wiki/Converting-to-the-new-gpu-back-end%28gpuarray%29

Using gpu device 0: Tesla K80 (CNMeM is disabled, cuDNN 5103)
WARNING (theano.sandbox.cuda): The cuda backend is deprecated and will be removed in the next release (v0.10).  Please switch to the gpuarray backend. You can get more information about how to switch at this URL:
 https://github.com/Theano/Theano/wiki/Converting-to-the-new-gpu-back-end%28gpuarray%29

WARNING (theano.sandbox.cuda): Ignoring call to use(2), GPU number 0 is already in use.


In [3]:
%matplotlib inline
import utils #; reload(utils)
from utils import *
from __future__ import division, print_function

Using Theano backend.


In [4]:
from keras.layers import TimeDistributed, Activation
from numpy.random import choice

In [5]:
limit_mem()

NameError: name 'limit_mem' is not defined

## Setup

We haven't really looked into the detail of how this works yet - so this is provided for self-study for those who are interested. We'll look at it closely next week.

In [6]:
path = get_file('nietzsche.txt', origin="https://s3.amazonaws.com/text-datasets/nietzsche.txt")
text = open(path).read().lower()
print('corpus length:', len(text))

corpus length: 600901


In [7]:
!tail {path} -n25

are thinkers who believe in the saints.


144

It stands to reason that this sketch of the saint, made upon the model
of the whole species, can be confronted with many opposing sketches that
would create a more agreeable impression. There are certain exceptions
among the species who distinguish themselves either by especial
gentleness or especial humanity, and perhaps by the strength of their
own personality. Others are in the highest degree fascinating because
certain of their delusions shed a particular glow over their whole
being, as is the case with the founder of christianity who took himself
for the only begotten son of God and hence felt himself sinless; so that
through his imagination--that should not be too harshly judged since the
whole of antiquity swarmed with sons of god--he attained the same goal,
the sense of complete sinlessness, complete irresponsibility, that can
now be attained by every individual through science.--In the same manner
I have viewed the saints of India

In [101]:
#path = 'data/wiki/'
#text = open(path+'small.txt').read().lower()
#print('corpus length:', len(text))

#text = text[0:1000000]

corpus length: 137587200


In [8]:
chars = sorted(list(set(text)))
vocab_size = len(chars)+1
print('total chars:', vocab_size)

total chars: 60


In [9]:
chars.insert(0, "\0")

In [10]:
''.join(chars[1:-6])

'\n !"\'(),-.0123456789:;=?[]_abcdefghijklmnopqrstuvwxyz'

In [11]:
char_indices = dict((c, i) for i, c in enumerate(chars))
indices_char = dict((i, c) for i, c in enumerate(chars))

In [12]:
idx = [char_indices[c] for c in text]

In [13]:
idx[:10]

[43, 45, 32, 33, 28, 30, 32, 1, 1, 1]

In [14]:
''.join(indices_char[i] for i in idx[:70])

'preface\n\n\nsupposing that truth is a woman--what then? is there not gro'

## Preprocess and create model

In [17]:
maxlen = 40
sentences = []
next_chars = []
for i in range(0, len(idx) - maxlen+1):
    sentences.append(idx[i: i + maxlen])
    next_chars.append(idx[i+1: i+maxlen+1])
print('nb sequences:', len(sentences))

nb sequences: 600862


In [18]:
sentences = np.concatenate([[np.array(o)] for o in sentences[:-2]])
next_chars = np.concatenate([[np.array(o)] for o in next_chars[:-2]])

In [19]:
sentences.shape, next_chars.shape

((600860, 40), (600860, 40))

In [20]:
n_fac = 24

In [21]:
model=Sequential([
        Embedding(vocab_size, n_fac, input_length=maxlen),
        LSTM(512, input_dim=n_fac,return_sequences=True, dropout_U=0.2, dropout_W=0.2,
             consume_less='gpu'),
        Dropout(0.2),
        LSTM(512, return_sequences=True, dropout_U=0.2, dropout_W=0.2,
             consume_less='gpu'),
        Dropout(0.2),
        TimeDistributed(Dense(vocab_size)),
        Activation('softmax')
    ])    

In [22]:
model.compile(loss='sparse_categorical_crossentropy', optimizer=Adam())

## Train

In [23]:
def print_example():
    seed_string="ethics is a basic foundation of all that"
    for i in range(320):
        x=np.array([char_indices[c] for c in seed_string[-40:]])[np.newaxis,:]
        preds = model.predict(x, verbose=0)[0][-1]
        preds = preds/np.sum(preds)
        next_char = choice(chars, p=preds)
        seed_string = seed_string + next_char
    print(seed_string)

In [24]:
model.fit(sentences, np.expand_dims(next_chars,-1), batch_size=64, nb_epoch=1)

Epoch 1/1
600860/600860 [==============================] - 1479s - loss: 1.5165     

In [25]:
print_example()

ethics is a basic foundation of all that
are not tears to ganner; there are unactually does not say: "it "equal truth_ in
the hard of the whole confoalment is not itself ouch all that the fact has got
with roueless and trample, daring, sternness, said.

[79] courageou), every conscience, and the
belief in the
second ages, seems to natural cases, in the
holy 


In [26]:
model.fit(sentences, np.expand_dims(next_chars,-1), batch_size=64, nb_epoch=1)

Epoch 1/1
600860/600860 [==============================] - 1471s - loss: 1.2940     

In [27]:
print_example()

ethics is a basic foundation of all that under belongs to put an almost
to
have,
conviction--that occasionally, my virtue is not deceived.

129. it vulgarizations, again in the events of point, however, which is little and an emotion; and there is should not be attitude what she is just have to truth. a question the modern
vigile.

292. does not hears as he 


In [28]:
model.optimizer.lr=0.001

In [29]:
model.fit(sentences, np.expand_dims(next_chars,-1), batch_size=64, nb_epoch=1)

Epoch 1/1
600860/600860 [==============================] - 1476s - loss: 1.2589     

In [30]:
print_example()

ethics is a basic foundation of all that because it dreads to the sake of life is only from rank and education, i see even the philosopher. that is to say, not yet all
nobility; the like to renounce what
has extinct by messame than the philosophers of life a new outbreak feeling, and to generally, the innocence
of jaxims and capacity for the straight still m


In [31]:
model.optimizer.lr=0.0001

In [32]:
model.fit(sentences, np.expand_dims(next_chars,-1), batch_size=64, nb_epoch=1)

Epoch 1/1
600860/600860 [==============================] - 1477s - loss: 1.2399     

In [33]:
print_example()

ethics is a basic foundation of all that are destroys succeeded with design: and the artist, and with it, that he permitted to be contemporary, under organization, are very inferible that are not different agreeable, be hand among men in the same last great service and dangerous advantage. the aights of running, motional men who
suffers them with something w


In [38]:
model.save_weights('data/char_rnn.h5')

In [35]:
model.optimizer.lr=0.00001

In [36]:
model.fit(sentences, np.expand_dims(next_chars,-1), batch_size=64, nb_epoch=1)

Epoch 1/1
600860/600860 [==============================] - 1470s - loss: 1.2266     

In [37]:
print_example()

ethics is a basic foundation of all that would make their
subtlety of questions. in the soul of everything subtle, self
sacrifice and with terrible lofty cultures, which fhints and possibilities: burning the religion of
their good art; and has always strange these metaphysicians of old astonishment.--we god, a discoverer, and corrition, not,
or, more conscio


In [39]:
model.fit(sentences, np.expand_dims(next_chars,-1), batch_size=64, nb_epoch=1)

Epoch 1/1
600860/600860 [==============================] - 1471s - loss: 1.2152     

In [40]:
print_example()

ethics is a basic foundation of all that
necessary.

61. here and often a
coedition. the
discipline of the ascetics, the morples of a belief as an old, then so empire to come in a bad critics, and understand,
nothing,
and more ever
more careful and scholarly a result of which religion and most consciences), about any nakily made a viwion and
accordingly. in



In [41]:
print_example()

ethics is a basic foundation of all that
everything
existed, ivaries mirror and self-exaggerative matters of evolution and unavoidably depthss and cannot
exist by them being comprised to be least in the most popular laws, the ditidity of the collectively and most renders the
involuntary honour--for it our vanity. it goes to look away in order to follow one's


In [42]:
model.save_weights('data/char_rnn.h5')